In [663]:
# Imports (External)
import numpy as np
import pandas as pd
import datetime
from datetime import datetime

from monthdelta import monthdelta
import xlrd
import xlsxwriter
from collections import OrderedDict
import pickle

import sys
sys.path.append('../')  

# Visualization/plotting imports
import matplotlib as mpl
import matplotlib.pyplot as plt

# Machine learning imports
import pywt
from pywt import wavedec, waverec
from scipy import signal
from statsmodels.robust import mad

import sklearn
import tensorflow as tf
import keras
from keras.layers import Input, Dense
from keras.models import Model, Sequential
from keras import optimizers
from keras import regularizers

# Internal Imports
from wsae_lstm.utils import pickle_load

In [664]:
dict_dataframes_index=pickle_load(path_filename="../data/interim/clean_data_index_interval.pickle")
#dict_dataframes_index.keys()

In [665]:
#dict_dataframes_index['csi300 index data'][1].drop(['date'],axis=1,inplace=True)

In [666]:
#dict_dataframes_index['csi300 index data'][1].reset_index(drop=True,inplace=True)

In [667]:
dict_dataframes_index['csi300 index data'][1].head()

open     high      low    close     volume  us dollar index  \
date                                                                         
2008-07-01  2799.20  2809.38  2690.18  2698.35  288515.85            72.34   
2008-07-02  2702.63  2745.94  2670.06  2699.60  279163.65            71.99   
2008-07-03  2654.48  2807.68  2617.26  2760.61  456603.05            72.73   
2008-07-04  2751.21  2783.85  2716.02  2741.85  379050.10            72.71   
2008-07-07  2747.61  2890.99  2747.61  2882.76  527320.24            72.71   

            shibor        macd         cci      atr         boll        ema20  \
date                                                                            
2008-07-01  2.5006 -213.078565 -128.949052  119.200  3173.475692  3033.748201   
2008-07-02  2.7238 -213.732249 -139.719688   75.875  3140.413385  3001.924277   
2008-07-03  2.5762 -206.941406 -112.113057  190.424  3109.044731  2978.942155   
2008-07-04  2.5632 -200.759162  -81.997539   67.825  3073.107115  2956.362140   
2008-07-07  2.5679 -182.386907   21.707767  149.133  3046.256923  2949.352699   

                 ma10     mtm6        ma5    mtm12       roc       smi  \
date                                                                     
2008-07-01  2851.2504  -91.594  2851.3262 -280.770 -9.424605 -0.097927   
2008-07-02  2822.0828 -152.318  2797.3382 -252.645 -8.557733 -0.026497   
2008-07-03  2820.8364 -208.925  2753.2792  -82.064 -2.886857 -0.031251   
2008-07-04  2810.0548 -239.055  2738.4454 -249.421 -8.338289 -0.017237   
2008-07-07  2819.3370   66.742  2756.6342  109.687  3.955427  0.010701   

                    wvad  
date                      
2008-07-01 -8.726278e+07  
2008-07-02 -1.095493e+08  
2008-07-03 -5.855737e+07  
2008-07-04 -7.467503e+07  
2008-07-07 -3.531151e+07

In [668]:
dict_dataframes_index['csi300 index data'][1].head()

open     high      low    close     volume  us dollar index  \
date                                                                         
2008-07-01  2799.20  2809.38  2690.18  2698.35  288515.85            72.34   
2008-07-02  2702.63  2745.94  2670.06  2699.60  279163.65            71.99   
2008-07-03  2654.48  2807.68  2617.26  2760.61  456603.05            72.73   
2008-07-04  2751.21  2783.85  2716.02  2741.85  379050.10            72.71   
2008-07-07  2747.61  2890.99  2747.61  2882.76  527320.24            72.71   

            shibor        macd         cci      atr         boll        ema20  \
date                                                                            
2008-07-01  2.5006 -213.078565 -128.949052  119.200  3173.475692  3033.748201   
2008-07-02  2.7238 -213.732249 -139.719688   75.875  3140.413385  3001.924277   
2008-07-03  2.5762 -206.941406 -112.113057  190.424  3109.044731  2978.942155   
2008-07-04  2.5632 -200.759162  -81.997539   67.825  3073.107115  2956.362140   
2008-07-07  2.5679 -182.386907   21.707767  149.133  3046.256923  2949.352699   

                 ma10     mtm6        ma5    mtm12       roc       smi  \
date                                                                     
2008-07-01  2851.2504  -91.594  2851.3262 -280.770 -9.424605 -0.097927   
2008-07-02  2822.0828 -152.318  2797.3382 -252.645 -8.557733 -0.026497   
2008-07-03  2820.8364 -208.925  2753.2792  -82.064 -2.886857 -0.031251   
2008-07-04  2810.0548 -239.055  2738.4454 -249.421 -8.338289 -0.017237   
2008-07-07  2819.3370   66.742  2756.6342  109.687  3.955427  0.010701   

                    wvad  
date                      
2008-07-01 -8.726278e+07  
2008-07-02 -1.095493e+08  
2008-07-03 -5.855737e+07  
2008-07-04 -7.467503e+07  
2008-07-07 -3.531151e+07

In [669]:
len(dict_dataframes_index['csi300 index data'][1])

612

In [670]:
len(dict_dataframes_index['csi300 index data'][1].columns)

19

In [671]:
len(dict_dataframes_index['csi300 index data'])

24

In [672]:
# train
dict_dataframes_index['csi300 index data'][1].index[0]

Timestamp('2008-07-01 00:00:00')

In [673]:
# validate
dict_dataframes_index['csi300 index data'][1].index[0] + monthdelta(24) 

Timestamp('2010-07-01 00:00:00')

In [674]:
# test
dict_dataframes_index['csi300 index data'][1].index[0] + monthdelta(27) 

Timestamp('2010-10-01 00:00:00')

In [753]:
def tvt_split(df):
    dict_dataframes = {}
    train = df.index[0]
    validate = df.index[0] + monthdelta(24) 
    test = df.index[0] + monthdelta(27) 
    test_end = df.index[0] + monthdelta(30) 
#     print("Train start:\n",train)
#     print("Train end/validate start:\n",validate)
#     print("Validate end/test start:\n",test)
#     print("Test end:\n",test_end)
    df_train = pd.DataFrame(df[(df.index >= train) & (df.index <= validate)])
    df_validate = pd.DataFrame(df[(df.index >= validate) & (df.index <= test)])
    df_test = pd.DataFrame(df[(df.index >= test) & (df.index <= test_end)])
    
    dict_dataframes ={1:df_train,2:df_validate,3:df_test}
    #return df_train,df_validate,df_test
    return dict_dataframes

# def dict_df_tvt_split(df):
#     subdict_dataframes = {}
#     split_count = 24
#     interval_index = 1
#     while split_count > 0:
#         df_train, df_validate, df_test = tvt_split(df[interval_index])
#         split_count -= 1
#         dict_dataframes[interval_index] = df_train, df_validate, df_test
#         interval_index += 1
#     return subdict_dataframes


# def dd_tvt_split(dict_dataframes):
#     subdict_dataframes = {}
#     for key in dict_dataframes:
#         print(key)
#         subdict_dataframes[key] = dict_df_tvt_split(dict_dataframes[key])
# #     for key in subdict_dataframes:
# #         subdict_dataframes[key] = {key-1: v for key, v in subdict_dataframes[key].items()}  
#     return subdict_dataframes

In [755]:
def dict_df_tvt_split2(df):
    subdict_dataframes = {}
    for key in df:
        subdict_dataframes[key] =tvt_split(df[key])
    return subdict_dataframes

#test =tvt_split(dict_dataframes_index['csi300 index data'][1])
test =dict_df_tvt_split2(dict_dataframes_index['csi300 index data'])
type(test)

dict

In [758]:
#test.keys()
len(test)

24

In [760]:
len(test[1])

3

In [764]:
test[1][1].head(1)

open     high      low    close     volume  us dollar index  \
date                                                                        
2008-07-01  2799.2  2809.38  2690.18  2698.35  288515.85            72.34   

            shibor        macd         cci    atr         boll        ema20  \
date                                                                          
2008-07-01  2.5006 -213.078565 -128.949052  119.2  3173.475692  3033.748201   

                 ma10    mtm6        ma5   mtm12       roc       smi  \
date                                                                   
2008-07-01  2851.2504 -91.594  2851.3262 -280.77 -9.424605 -0.097927   

                    wvad  
date                      
2008-07-01 -8.726278e+07

In [765]:
test[1][2].head(1)

open    high      low    close     volume  us dollar index  \
date                                                                        
2010-07-01  2557.92  2574.1  2524.57  2526.07  328576.46            84.55   

            shibor       macd         cci     atr         boll        ema20  \
date                                                                          
2010-07-01  2.2492 -68.405561 -199.061153  49.525  2742.562654  2713.585325   

                 ma10     mtm6        ma5    mtm12       roc       smi  \
date                                                                     
2010-07-01  2691.0766 -232.424  2626.8448 -223.952 -8.143641 -0.063088   

                    wvad  
date                      
2010-07-01 -9.298846e+07

In [766]:
test[1][3].head(1)

open     high      low    close    volume  us dollar index  \
date                                                                        
2010-10-08  2965.65  3055.84  2963.24  3044.23  999947.2             77.2   

            shibor       macd         cci      atr         boll        ema20  \
date                                                                           
2010-10-08  1.7325  14.071181  187.594016  120.262  2912.040962  2913.539251   

                 ma10     mtm6       ma5    mtm12      roc       smi  \
date                                                                   
2010-10-08  2898.0211  194.405  2928.111  111.679  3.80825  0.043045   

                    wvad  
date                      
2010-10-08  1.079573e+08

In [751]:
tvt_dict = dd_tvt_split(dict_dataframes_index)

csi300 index data
{1:                open     high      low    close     volume  us dollar index  \
date                                                                         
2008-07-01  2799.20  2809.38  2690.18  2698.35  288515.85            72.34   
2008-07-02  2702.63  2745.94  2670.06  2699.60  279163.65            71.99   
2008-07-03  2654.48  2807.68  2617.26  2760.61  456603.05            72.73   
2008-07-04  2751.21  2783.85  2716.02  2741.85  379050.10            72.71   
2008-07-07  2747.61  2890.99  2747.61  2882.76  527320.24            72.71   
2008-07-08  2900.57  2939.14  2841.07  2901.84  542480.78            72.96   
2008-07-09  2927.00  3015.27  2927.00  3015.13  693569.68            72.59   
2008-07-10  2970.98  3056.91  2950.20  2973.73  616495.54            72.49   
2008-07-11  2962.86  2988.20  2913.87  2953.50  442871.01            71.91   
2008-07-14  2927.24  2996.59  2917.02  2975.87  345750.43            71.96   
2008-07-15  2987.06  2997.67  2849.20  285

{1:                open     high      low    close     volume  us dollar index  \
date                                                                         
2008-07-01  2799.20  2809.38  2690.18  2698.35  288515.85            72.34   
2008-07-02  2702.63  2745.94  2670.06  2699.60  279163.65            71.99   
2008-07-03  2654.48  2807.68  2617.26  2760.61  456603.05            72.73   
2008-07-04  2751.21  2783.85  2716.02  2741.85  379050.10            72.71   
2008-07-07  2747.61  2890.99  2747.61  2882.76  527320.24            72.71   
2008-07-08  2900.57  2939.14  2841.07  2901.84  542480.78            72.96   
2008-07-09  2927.00  3015.27  2927.00  3015.13  693569.68            72.59   
2008-07-10  2970.98  3056.91  2950.20  2973.73  616495.54            72.49   
2008-07-11  2962.86  2988.20  2913.87  2953.50  442871.01            71.91   
2008-07-14  2927.24  2996.59  2917.02  2975.87  345750.43            71.96   
2008-07-15  2987.06  2997.67  2849.20  2852.98  472927.59   

{1:                open     high      low    close     volume  us dollar index  \
date                                                                         
2008-07-01  2799.20  2809.38  2690.18  2698.35  288515.85            72.34   
2008-07-02  2702.63  2745.94  2670.06  2699.60  279163.65            71.99   
2008-07-03  2654.48  2807.68  2617.26  2760.61  456603.05            72.73   
2008-07-04  2751.21  2783.85  2716.02  2741.85  379050.10            72.71   
2008-07-07  2747.61  2890.99  2747.61  2882.76  527320.24            72.71   
2008-07-08  2900.57  2939.14  2841.07  2901.84  542480.78            72.96   
2008-07-09  2927.00  3015.27  2927.00  3015.13  693569.68            72.59   
2008-07-10  2970.98  3056.91  2950.20  2973.73  616495.54            72.49   
2008-07-11  2962.86  2988.20  2913.87  2953.50  442871.01            71.91   
2008-07-14  2927.24  2996.59  2917.02  2975.87  345750.43            71.96   
2008-07-15  2987.06  2997.67  2849.20  2852.98  472927.59   

{1:                open     high      low    close     volume  us dollar index  \
date                                                                         
2008-07-01  2799.20  2809.38  2690.18  2698.35  288515.85            72.34   
2008-07-02  2702.63  2745.94  2670.06  2699.60  279163.65            71.99   
2008-07-03  2654.48  2807.68  2617.26  2760.61  456603.05            72.73   
2008-07-04  2751.21  2783.85  2716.02  2741.85  379050.10            72.71   
2008-07-07  2747.61  2890.99  2747.61  2882.76  527320.24            72.71   
2008-07-08  2900.57  2939.14  2841.07  2901.84  542480.78            72.96   
2008-07-09  2927.00  3015.27  2927.00  3015.13  693569.68            72.59   
2008-07-10  2970.98  3056.91  2950.20  2973.73  616495.54            72.49   
2008-07-11  2962.86  2988.20  2913.87  2953.50  442871.01            71.91   
2008-07-14  2927.24  2996.59  2917.02  2975.87  345750.43            71.96   
2008-07-15  2987.06  2997.67  2849.20  2852.98  472927.59   

{1:                open     high      low    close     volume  us dollar index  \
date                                                                         
2008-07-01  2799.20  2809.38  2690.18  2698.35  288515.85            72.34   
2008-07-02  2702.63  2745.94  2670.06  2699.60  279163.65            71.99   
2008-07-03  2654.48  2807.68  2617.26  2760.61  456603.05            72.73   
2008-07-04  2751.21  2783.85  2716.02  2741.85  379050.10            72.71   
2008-07-07  2747.61  2890.99  2747.61  2882.76  527320.24            72.71   
2008-07-08  2900.57  2939.14  2841.07  2901.84  542480.78            72.96   
2008-07-09  2927.00  3015.27  2927.00  3015.13  693569.68            72.59   
2008-07-10  2970.98  3056.91  2950.20  2973.73  616495.54            72.49   
2008-07-11  2962.86  2988.20  2913.87  2953.50  442871.01            71.91   
2008-07-14  2927.24  2996.59  2917.02  2975.87  345750.43            71.96   
2008-07-15  2987.06  2997.67  2849.20  2852.98  472927.59   

...

{1:                open     high      low    close     volume  us dollar index  \
date                                                                         
2008-07-01  2799.20  2809.38  2690.18  2698.35  288515.85            72.34   
2008-07-02  2702.63  2745.94  2670.06  2699.60  279163.65            71.99   
2008-07-03  2654.48  2807.68  2617.26  2760.61  456603.05            72.73   
2008-07-04  2751.21  2783.85  2716.02  2741.85  379050.10            72.71   
2008-07-07  2747.61  2890.99  2747.61  2882.76  527320.24            72.71   
2008-07-08  2900.57  2939.14  2841.07  2901.84  542480.78            72.96   
2008-07-09  2927.00  3015.27  2927.00  3015.13  693569.68            72.59   
2008-07-10  2970.98  3056.91  2950.20  2973.73  616495.54            72.49   
2008-07-11  2962.86  2988.20  2913.87  2953.50  442871.01            71.91   
2008-07-14  2927.24  2996.59  2917.02  2975.87  345750.43            71.96   
2008-07-15  2987.06  2997.67  2849.20  2852.98  472927.59   

{1:                open     high      low    close     volume  us dollar index  \
date                                                                         
2008-07-01  2799.20  2809.38  2690.18  2698.35  288515.85            72.34   
2008-07-02  2702.63  2745.94  2670.06  2699.60  279163.65            71.99   
2008-07-03  2654.48  2807.68  2617.26  2760.61  456603.05            72.73   
2008-07-04  2751.21  2783.85  2716.02  2741.85  379050.10            72.71   
2008-07-07  2747.61  2890.99  2747.61  2882.76  527320.24            72.71   
2008-07-08  2900.57  2939.14  2841.07  2901.84  542480.78            72.96   
2008-07-09  2927.00  3015.27  2927.00  3015.13  693569.68            72.59   
2008-07-10  2970.98  3056.91  2950.20  2973.73  616495.54            72.49   
2008-07-11  2962.86  2988.20  2913.87  2953.50  442871.01            71.91   
2008-07-14  2927.24  2996.59  2917.02  2975.87  345750.43            71.96   
2008-07-15  2987.06  2997.67  2849.20  2852.98  472927.59   

{1:                open     high      low    close     volume  us dollar index  \
date                                                                         
2008-07-01  2799.20  2809.38  2690.18  2698.35  288515.85            72.34   
2008-07-02  2702.63  2745.94  2670.06  2699.60  279163.65            71.99   
2008-07-03  2654.48  2807.68  2617.26  2760.61  456603.05            72.73   
2008-07-04  2751.21  2783.85  2716.02  2741.85  379050.10            72.71   
2008-07-07  2747.61  2890.99  2747.61  2882.76  527320.24            72.71   
2008-07-08  2900.57  2939.14  2841.07  2901.84  542480.78            72.96   
2008-07-09  2927.00  3015.27  2927.00  3015.13  693569.68            72.59   
2008-07-10  2970.98  3056.91  2950.20  2973.73  616495.54            72.49   
2008-07-11  2962.86  2988.20  2913.87  2953.50  442871.01            71.91   
2008-07-14  2927.24  2996.59  2917.02  2975.87  345750.43            71.96   
2008-07-15  2987.06  2997.67  2849.20  2852.98  472927.59   

{1:                open     high      low    close     volume  us dollar index  \
date                                                                         
2008-07-01  2799.20  2809.38  2690.18  2698.35  288515.85            72.34   
2008-07-02  2702.63  2745.94  2670.06  2699.60  279163.65            71.99   
2008-07-03  2654.48  2807.68  2617.26  2760.61  456603.05            72.73   
2008-07-04  2751.21  2783.85  2716.02  2741.85  379050.10            72.71   
2008-07-07  2747.61  2890.99  2747.61  2882.76  527320.24            72.71   
2008-07-08  2900.57  2939.14  2841.07  2901.84  542480.78            72.96   
2008-07-09  2927.00  3015.27  2927.00  3015.13  693569.68            72.59   
2008-07-10  2970.98  3056.91  2950.20  2973.73  616495.54            72.49   
2008-07-11  2962.86  2988.20  2913.87  2953.50  442871.01            71.91   
2008-07-14  2927.24  2996.59  2917.02  2975.87  345750.43            71.96   
2008-07-15  2987.06  2997.67  2849.20  2852.98  472927.59   

KeyboardInterrupt: 

In [677]:
len(tvt_dict['csi300 index data'])

24

In [678]:
type(tvt_dict['csi300 index data'])

dict

In [679]:
tvt_dict['csi300 index data'].keys()

dict_keys([1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24])

In [686]:
type(tvt_dict['csi300 index data'][1][0])

int

In [687]:
len(tvt_dict['csi300 index data'][1])

3

In [688]:
#len(tvt_dict['csi300 index data'][1][0])

In [689]:
type(tvt_dict['csi300 index data'][1][0])

int

In [690]:
tvt_dict['csi300 index data'][1][0].head(1)

AttributeError: 'int' object has no attribute 'head'

In [691]:
tvt_dict['csi300 index data'][1][1].head(1)

AttributeError: 'int' object has no attribute 'head'

In [695]:
tvt_dict['csi300 index data'][1][2].head()

AttributeError: 'int' object has no attribute 'head'

In [693]:
# dict_dataframes = {}
# for key in dict_dataframes_index:
#     print(key)
#     dict_dataframes[key] = dict_df_tvt_split(dict_dataframes_index[key])
# dict_dataframes['csi300 index data'] = {k-1: v for k, v in dict_dataframes['csi300 index data'].items()}

In [ ]:
#len(dict_dataframes)

In [ ]:
#len(dict_dataframes['csi300 index data'])

In [ ]:
#type(dict_dataframes['csi300 index data'])

In [ ]:
#dict_dataframes['csi300 index data'].keys()

In [ ]:
#dict_dataframes['csi300 index data'] = {k-1: v for k, v in dict_dataframes['csi300 index data'].items()}

In [ ]:
#dict_dataframes['csi300 index data'].keys()

In [ ]:
#len(dict_dataframes['csi300 index data'][1][1])

In [ ]:
#dict_dataframes['csi300 index data'][1][0].head(1)

In [ ]:
#dict_dataframes['csi300 index data'][1][1].head(1)

In [ ]:
#dict_dataframes['csi300 index data'][1][2].head(1)

In [ ]:
# def dict_df_tvt_split_test(dict_dataframes):
#     subdict_dataframes = {}
#     split_count = 24
#     interval_index = 1
#     for dataframe in dict_dataframes:
#         subdict_dataframes[dataframe][interval_index] = dict_tvt_split(dict_dataframes[dataframe])
#         interval_index += 1
#     return subdict_dataframes

In [ ]:
#train.head(2)

In [ ]:
#validate.head(2)

In [ ]:
#test.head(2)